In [1]:
import nltk
import json
from itertools import permutations

In [2]:
def getSentenceTags():
    result = []
    kalimat = []
    c=0
    with open('file.txt') as data:
        while True:
            tag = []
            sentence_id= data.readline()
            sentence_id= sentence_id.lower()
            if(len(sentence_id.strip())==0):
                continue
            if "#eof" in sentence_id:
                break
            sentence = ""
            if("#" in sentence_id):
                if("# text" in sentence_id):
                    c+=1
                    x = sentence_id.split("# text = ")
                    x = nltk.word_tokenize(x[1])
                    x.insert(0, "<start>")
                    kalimat.append(x)
                    for m in range(len(x)):
                        y = data.readline()
                        if ("#" in y):
                            break
                        y = y.replace("\n", "")
                        y = y.split("\t")
                        if(len(y)<3):
                            continue
                        if(y[2]=="_"):
                            tagnya = y[3]
                        else:
                            tagnya = y[2]
                        tag.append(tagnya)
                    result.append(tag)
    return kalimat, result

In [3]:
#i = tag 1
#j = tag 2
def fillTransitionTable(i, j, sentence, sentence_tag):
    count = 0
    for n in range(len(sentence)-1):
        if(sentence_tag[n] == i):
            if(sentence_tag[n+1] == j):
                count +=1
    print("INI BOI",sentence_tag[n])



    return count

In [4]:

def buildTransitionTable(info, all_tag):
    # sentence_tag.insert(0, "start")
    # for i in range(len(sentence)):
    transition_table ={}
    #iterasi tiap kalimat di data
    for i in range(len(info[0])):
        info[1][i].insert(0, "start")
        #iterasi tiap kata di kalimat
        for j in range(len(info[1][i])-2):
            # if(info[1][i][j])
            # print(info[1][i][2])
            # if(len(info[1][j]) != len(info[0][j])):
            #     print(i,len(info[1][j]), len(info[0][j]))
            #     print(info[0][j])
            #     print(info[1][j])
            #     print("==================================")
            # print (info[1][i][j], "|", info[0][i][j])
            #masukan current word's tag dan next word tag ke dict
            #kalau tag pertama sudah ada di table
            a = info[1][i][j]
            b = info[1][i][j+1]
            if(a in transition_table):
                #kalau tag ke 2 sudah ada di table
                if(b in transition_table[a]):
                    transition_table[a][b] +=1
                #kalau tag ke 2 blm ada di table
                else:
                    transition_table[a][b] = 1
            else:
                transition_table[a] = {}
                transition_table[a][b] = 1
    transition_table_sum ={}
    result = {}
    for i in transition_table:
        for j in transition_table[i]:
            transition_table_sum[i] = 0
            
            #klo kt ada di result
            if(i not in result):
                result[i] ={}
            result[i][j] =0
    for i in transition_table:
        for j in transition_table[i]:
            # print(i,j,transition_table[i][j])
            transition_table_sum[i] += transition_table[i][j]
    # print(transition_table_sum)

    for i in transition_table:
        for j in transition_table[i]:
            # print(i, j, transition_table[i][j])
            # print(i, transition_table_sum[i])
            result[i][j] = transition_table[i][j]/ float(transition_table_sum[i])
            # print(transition_table[i][j])

    return result

In [5]:
def getAllAvailableTags():
    result = []
    tagnya=""
    kalimat = []
    with open('file.txt') as data:
        while True:
            sentence_id= data.readline()
            sentence_id= sentence_id.lower()
            if(len(sentence_id.strip())==0):
                continue
            if "#eof" in sentence_id:
                break
            sentence = ""
            if("#" in sentence_id):
                continue

            else:
                sentence = sentence_id
                sentence = sentence.split("\t")
                if(sentence[2]=="_"):
                    tagnya = sentence[3]
                else:
                    tagnya = sentence[2]
                if(tagnya not in result):
                    result.append(tagnya)
    return result


In [6]:
def read():
    kamus = {}
    sentence_list = []
    with open('file.txt') as data:
        while True:
            sentence_id = data.readline()
            sentence_id = sentence_id.lower()
            if len(sentence_id.strip()) == 0 :
                continue
            if "#eot#" in sentence_id:
            	break
            sentence= ""
            if("#" in sentence_id):
                if("# text" in sentence_id):
                    sentence_list.append(sentence_id)
            else:
                sentence = sentence_id
                sentence = sentence.split("\t")
                if(sentence[2]=="_"):
                    tagnya = sentence[3]
                else:
                    tagnya = sentence[2]
                # print(sentence[1], tagnya)
                #kalau kata tsb sudah ada di kamus
                if(sentence[1] in kamus):
                    #kalau tag nya sudah ada terdaftar di kata tsb
                    if(tagnya in kamus[sentence[1]]):
                        #frequensi +1
                        kamus[sentence[1]][tagnya] +=1
                    #kalau tagnya belum terdaftar di kata tsb
                    else:
                        kamus[sentence[1]][tagnya] = 1
                #kalau kata tsb blm terdaftar di kamus
                else:
                    kamus[sentence[1]] = {}
                    kamus[sentence[1]][tagnya] = 1
    return kamus, sentence_list


In [7]:
def readTestData():
    with open('file.txt') as data:
        sentence = data.readline()
        #loop sampai muncul eot, atau end of training data
        while True:
            if("#eot#" in sentence):
                break
            else:
                sentence = data.readline()
        test_sentence = []
        #loop dari awal test data sampai end of file
        while True:
            if("#eof#" in sentence):
                break
            else:
                if("# text" in sentence):
                    sentence = sentence.lower()
                    sentence = sentence.split("=")
                    test_sentence.append(sentence[1])
                sentence = data.readline()

    return test_sentence


In [8]:
#ambil semua tag yg posible dari 1 data
def getwordAllTag(kata,kamus):
    #loop tiap kata
    try:
        get = kamus[kata]
    except KeyError:
        get = {'unknown' : 0}
    return (kata, get)


In [9]:
def getEmission(get):
    emission = {}
    n= 0
    for i in get:
        n += get[i]
    for i in get:
        if (n==0):
            emission[i] = 0
        else:
            emission[i] = get[i]/float(n)
            # print(get, i, "jumlah n: ", n)
    return emission

In [10]:
def loadKalimat():
    with open('file.txt') as data:
        sentence = data.readline()
        while "#eot" not in sentence:
            sentence = data.readline()
        hasil =[]
        while True:
            sentence = data.readline()
            sentence = sentence.lower()
            # if "#eot" in sentence:
            #     continue
            if "#eof" in sentence:
                break
            if "# text = " in sentence:
                # print(sentence)
                sentence = sentence.split("# text =")
                sentence = sentence[1]
                sentence = sentence.replace("\n", "")
                hasil.append(sentence)
    return hasil

In [11]:
a= read()

In [13]:
b= getSentenceTags()

In [14]:
all_tag = getAllAvailableTags()

In [15]:
transition_table = buildTransitionTable(b, all_tag) 

In [16]:
c=loadKalimat()

In [17]:
tags = getAllAvailableTags()
tags.insert(0, "<start>")

In [18]:
#GET TAG BASED ON EMISSION TABLE
for sentences in b[0]:
    for j in sentences:
        if(j=="<start>"):
            continue
        word_tag = getwordAllTag(j, a[0])
        word_emission = getEmission(word_tag[1])
        print(j, word_emission)

sembungan {'propn': 1.0}
adalah {'verb': 0.007444168734491315, 'aux': 0.9925558312655087}
sebuah {'det': 1.0}
desa {'noun': 0.8148148148148148, 'propn': 0.18518518518518517}
yang {'cconj': 0.0029106029106029108, 'pron': 0.992931392931393, 'propn': 0.0029106029106029108, 'noun': 0.0008316008316008316, 'part': 0.0004158004158004158}
terletak {'verb': 1.0}
di {'verb': 0.005869797225186766, 'propn': 0.0032017075773745998, 'cconj': 0.0026680896478121665, 'adp': 0.9861259338313767, 'sconj': 0.0016008537886872999, 'x': 0.0005336179295624333}
kecamatan {'noun': 0.40948275862068967, 'propn': 0.5905172413793104}
kejajar {'propn': 1.0}
, {'punct': 1.0}
kabupaten {'noun': 0.13744075829383887, 'propn': 0.8625592417061612}
wonosobo {'propn': 1.0}
, {'punct': 1.0}
jawa {'noun': 0.015503875968992248, 'propn': 0.9844961240310077}
tengah {'adp': 0.034482758620689655, 'noun': 0.09195402298850575, 'adj': 0.05747126436781609, 'propn': 0.8160919540229885}
, {'punct': 1.0}
indonesia {'noun': 0.00849858356940

bahwa {'cconj': 0.012738853503184714, 'pron': 0.03821656050955414, 'adp': 0.12101910828025478, 'sconj': 0.821656050955414, 'adv': 0.006369426751592357}
mereka {'pron': 1.0}
bisa {'adv': 0.9512195121951219, 'verb': 0.04878048780487805}
menjadi {'verb': 0.9898305084745763, 'adp': 0.006779661016949152, 'noun': 0.003389830508474576}
sangat {'adv': 1.0}
solid {'adj': 1.0}
karena {'cconj': 0.1989247311827957, 'adp': 0.0913978494623656, 'sconj': 0.7096774193548387}
mereka {'pron': 1.0}
bertiga {'verb': 1.0}
, {'punct': 1.0}
kalau {'sconj': 1.0}
jalan {'verb': 0.05405405405405406, 'noun': 0.7027027027027027, 'propn': 0.24324324324324326}
sendiri {'propn': 0.015151515151515152, 'adv': 0.13636363636363635, 'pron': 0.10606060606060606, 'det': 0.045454545454545456, 'noun': 0.015151515151515152, 'adj': 0.6818181818181818}
- {'punct': 1.0}
sendiri {'propn': 0.015151515151515152, 'adv': 0.13636363636363635, 'pron': 0.10606060606060606, 'det': 0.045454545454545456, 'noun': 0.015151515151515152, 'adj':

komunis {'noun': 0.5555555555555556, 'propn': 0.4444444444444444}
muda {'noun': 0.05263157894736842, 'adj': 0.8947368421052632, 'propn': 0.05263157894736842}
dari {'cconj': 0.0011013215859030838, 'adp': 0.9977973568281938, 'propn': 0.0011013215859030838}
belanda {'propn': 1.0}
bernama {'verb': 0.9777777777777777, 'propn': 0.022222222222222223}
marinus {'propn': 1.0}
van {'propn': 1.0}
der {'propn': 1.0}
lubbe {'propn': 1.0}
pada {'adp': 1.0}
27 {'num': 1.0}
februari {'noun': 0.125, 'propn': 0.875}
1933 {'num': 1.0}
. {'punct': 0.9997731911998186, 'propn': 0.00022680880018144704}
wewe {'propn': 1.0}
gombel {'propn': 1.0}
biasanya {'adv': 1.0}
digambarkan {'verb': 1.0}
dengan {'cconj': 0.003293084522502744, 'adp': 0.995609220636663, 'sconj': 0.0010976948408342481}
sosok {'noun': 1.0}
wanita {'noun': 0.9333333333333333, 'propn': 0.06666666666666667}
tua {'adj': 0.8571428571428571, 'propn': 0.14285714285714285}
keriput {'verb': 1.0}
dengan {'cconj': 0.003293084522502744, 'adp': 0.995609220

* {'sym': 1.0}
pusat {'noun': 0.6037735849056604, 'adj': 0.03773584905660377, 'propn': 0.3584905660377358}
pendidikan {'noun': 0.8108108108108109, 'propn': 0.1891891891891892}
dan {'cconj': 0.9945627548708654, 'sconj': 0.0018124150430448573, 'propn': 0.0036248300860897147}
pelatihan {'noun': 0.75, 'propn': 0.25}
kearsipan {'propn': 1.0}
* {'sym': 1.0}
direktorat {'noun': 0.1, 'propn': 0.9}
akuisisi {'noun': 0.6666666666666666, 'propn': 0.3333333333333333}
* {'sym': 1.0}
direktorat {'noun': 0.1, 'propn': 0.9}
pengolahan {'noun': 0.875, 'propn': 0.125}
* {'sym': 1.0}
direktorat {'noun': 0.1, 'propn': 0.9}
preservasi {'propn': 1.0}
* {'sym': 1.0}
direktorat {'noun': 0.1, 'propn': 0.9}
pemanfaatan {'noun': 0.5, 'propn': 0.5}
* {'sym': 1.0}
pusat {'noun': 0.6037735849056604, 'adj': 0.03773584905660377, 'propn': 0.3584905660377358}
pengkajian {'propn': 1.0}
dan {'cconj': 0.9945627548708654, 'sconj': 0.0018124150430448573, 'propn': 0.0036248300860897147}
pengembangan {'noun': 0.75, 'propn': 0

anak {'noun': 0.9787234042553191, 'propn': 0.02127659574468085}
setelah {'adv': 0.07142857142857142, 'cconj': 0.017857142857142856, 'adp': 0.6547619047619048, 'sconj': 0.25595238095238093}
harmagedon {'propn': 1.0}
, {'punct': 1.0}
bukankah {'part': 1.0}
selayaknya {'adv': 1.0}
, {'punct': 1.0}
sesuai {'adp': 0.25, 'adj': 0.75}
dengan {'cconj': 0.003293084522502744, 'adp': 0.995609220636663, 'sconj': 0.0010976948408342481}
kitab {'noun': 0.7857142857142857, 'propn': 0.21428571428571427}
suci {'adj': 0.4, 'propn': 0.6}
, {'punct': 1.0}
bila {'cconj': 0.047619047619047616, 'noun': 0.047619047619047616, 'sconj': 0.9047619047619048}
mereka {'pron': 1.0}
melakukannya {'verb': 1.0}
segera {'adv': 0.95, 'noun': 0.05}
sebelum {'adv': 0.17391304347826086, 'cconj': 0.021739130434782608, 'adp': 0.6956521739130435, 'sconj': 0.08695652173913043, 'propn': 0.021739130434782608}
harmagedon {'propn': 1.0}
? {'punct': 1.0}
di {'verb': 0.005869797225186766, 'propn': 0.0032017075773745998, 'cconj': 0.0026

...

dan {'cconj': 0.9945627548708654, 'sconj': 0.0018124150430448573, 'propn': 0.0036248300860897147}
bahasa {'noun': 0.8992248062015504, 'propn': 0.10077519379844961}
habo {'propn': 1.0}
. {'punct': 0.9997731911998186, 'propn': 0.00022680880018144704}
filum {'noun': 1.0}
ini {'det': 0.9966960352422908, 'noun': 0.003303964757709251}
tidak {'adv': 0.06804733727810651, 'part': 0.9289940828402367, 'propn': 0.0029585798816568047}
bersegmen {'verb': 1.0}
dan {'cconj': 0.9945627548708654, 'sconj': 0.0018124150430448573, 'propn': 0.0036248300860897147}
berukuran {'verb': 1.0}
panjang {'noun': 0.4666666666666667, 'adj': 0.5333333333333333}
serta {'cconj': 0.9259259259259259, 'verb': 0.037037037037037035, 'adp': 0.012345679012345678, 'sconj': 0.012345679012345678, 'adj': 0.012345679012345678}
tipis {'adj': 1.0}
. {'punct': 0.9997731911998186, 'propn': 0.00022680880018144704}
pada {'adp': 1.0}
tahun {'verb': 0.0016891891891891893, 'noun': 0.9881756756756757, 'propn': 0.010135135135135136}
2000 {'num

sebagai {'adp': 0.9978260869565218, 'propn': 0.002173913043478261}
salah {'verb': 0.0064516129032258064, 'propn': 0.0064516129032258064, 'adv': 0.0064516129032258064, 'det': 0.832258064516129, 'noun': 0.14193548387096774, 'adj': 0.0064516129032258064}
satu {'det': 0.6201550387596899, 'noun': 0.06201550387596899, 'adj': 0.003875968992248062, 'num': 0.29844961240310075, 'propn': 0.015503875968992248}
pemain {'noun': 1.0}
terbaik {'adj': 0.4, 'propn': 0.6}
dalam {'adp': 0.9796557120500783, 'noun': 0.012519561815336464, 'adj': 0.004694835680751174, 'propn': 0.003129890453834116}
sejarah {'noun': 1.0}
sepak {'noun': 0.9230769230769231, 'propn': 0.07692307692307693}
bola {'noun': 0.9565217391304348, 'propn': 0.043478260869565216}
amerika {'propn': 1.0}
. {'punct': 0.9997731911998186, 'propn': 0.00022680880018144704}
maine {'propn': 1.0}
- {'punct': 1.0}
et {'propn': 1.0}
- {'punct': 1.0}
loire {'propn': 1.0}
ialah {'aux': 1.0}
sebuah {'det': 1.0}
departemen {'noun': 0.5454545454545454, 'prop

sampai {'adv': 0.01098901098901099, 'verb': 0.07692307692307693, 'adp': 0.8901098901098901, 'sconj': 0.01098901098901099, 'propn': 0.01098901098901099}
saat {'adv': 0.031055900621118012, 'cconj': 0.006211180124223602, 'adp': 0.14285714285714285, 'noun': 0.6708074534161491, 'sconj': 0.14906832298136646}
ini {'det': 0.9966960352422908, 'noun': 0.003303964757709251}
tercatat {'verb': 0.8333333333333334, 'propn': 0.16666666666666666}
sebagai {'adp': 0.9978260869565218, 'propn': 0.002173913043478261}
pembalap {'adp': 0.25, 'noun': 0.75}
pertama {'num': 0.5869565217391305, 'propn': 0.021739130434782608, 'noun': 0.007246376811594203, 'sconj': 0.007246376811594203, 'adj': 0.37681159420289856}
dan {'cconj': 0.9945627548708654, 'sconj': 0.0018124150430448573, 'propn': 0.0036248300860897147}
satu {'det': 0.6201550387596899, 'noun': 0.06201550387596899, 'adj': 0.003875968992248062, 'num': 0.29844961240310075, 'propn': 0.015503875968992248}
- {'punct': 1.0}
satunya {'det': 0.6666666666666666, 'noun

, {'punct': 1.0}
sebuah {'det': 1.0}
wilayah {'noun': 0.9122807017543859, 'propn': 0.08771929824561403}
di {'verb': 0.005869797225186766, 'propn': 0.0032017075773745998, 'cconj': 0.0026680896478121665, 'adp': 0.9861259338313767, 'sconj': 0.0016008537886872999, 'x': 0.0005336179295624333}
koln {'propn': 1.0}
, {'punct': 1.0}
kekaisaran {'noun': 0.9166666666666666, 'propn': 0.08333333333333333}
romawi {'propn': 1.0}
. {'punct': 0.9997731911998186, 'propn': 0.00022680880018144704}
syahiduddin {'propn': 1.0}
kemudian {'adv': 0.9197530864197531, 'cconj': 0.006172839506172839, 'sconj': 0.06172839506172839, 'adj': 0.012345679012345678}
meminta {'verb': 1.0}
kepada {'adp': 1.0}
kakaknya {'noun': 1.0}
, {'punct': 1.0}
huwaenah {'noun': 1.0}
untuk {'adp': 0.9972527472527473, 'propn': 0.0027472527472527475}
membantunya {'verb': 1.0}
mengurus {'verb': 1.0}
santri {'noun': 1.0}
- {'punct': 1.0}
santri {'noun': 1.0}
putri {'noun': 0.2857142857142857, 'adj': 0.047619047619047616, 'propn': 0.666666666

memformulasikan {'unknown': 0}
dan {'cconj': 0.9945627548708654, 'sconj': 0.0018124150430448573, 'propn': 0.0036248300860897147}
berhasil {'verb': 1.0}
mengetes {'verb': 1.0}
beberapa {'det': 0.986013986013986, 'noun': 0.006993006993006993, 'adj': 0.006993006993006993}
hasil {'noun': 1.0}
dari {'cconj': 0.0011013215859030838, 'adp': 0.9977973568281938, 'propn': 0.0011013215859030838}
dinamika {'noun': 1.0}
mekanik {'noun': 1.0}
, {'punct': 1.0}
terutama {'adv': 0.9393939393939394, 'adj': 0.06060606060606061}
hukum {'noun': 0.8214285714285714, 'propn': 0.17857142857142858}
inert {'unknown': 0}
. {'punct': 0.9997731911998186, 'propn': 0.00022680880018144704}
rumak {'unknown': 0}
adalah {'verb': 0.007444168734491315, 'aux': 0.9925558312655087}
desa {'noun': 0.8148148148148148, 'propn': 0.18518518518518517}
yang {'cconj': 0.0029106029106029108, 'pron': 0.992931392931393, 'propn': 0.0029106029106029108, 'noun': 0.0008316008316008316, 'part': 0.0004158004158004158}
berada {'verb': 1.0}
di {'

In [20]:
#print count
print(a[0])

{'kampak': {'noun': 1}, 'tour': {'noun': 1, 'propn': 1}, 'buahan': {'noun': 3}, 'mengidolakan': {'verb': 1}, 'suara': {'noun': 18, 'propn': 6}, 'penghulu': {'noun': 1}, 'נביאים': {'noun': 2}, 'merawatnya': {'verb': 1}, 'seafood': {'propn': 1}, 'charminar': {'propn': 1}, 'digambarkan': {'verb': 6}, 'sawahlunto': {'propn': 1}, 'armory': {'propn': 1}, 'maskot': {'noun': 1}, 'ficus': {'propn': 1}, 'temu': {'noun': 1, 'propn': 1}, 'letakknya': {'verb': 1}, 'rahardjo': {'propn': 1}, 'membidani': {'verb': 1}, 'diorganisasi': {'verb': 1}, 'cubensis': {'propn': 1}, 'dilewati': {'verb': 2}, 'kesimpulannya': {'noun': 1}, '1942': {'num': 1}, 'pedesaan': {'noun': 5}, 'zimmerman': {'propn': 1}, 'ottoman': {'propn': 1}, 'agathis': {'propn': 1}, 'clementina': {'propn': 1}, 'dasar': {'noun': 9, 'adj': 22, 'propn': 11}, 'tarik': {'verb': 2, 'propn': 1}, 'djie': {'propn': 1}, 'ukrida': {'propn': 1}, 'protein': {'noun': 9, 'propn': 1}, 'jaim': {'propn': 1}, 'mengimbas': {'verb': 1}, 'dikecamatan': {'noun'